In [ ]:
import numpy as np
import matplotlib.pyplot as plt

import astropy
import astropy.units as u
from astropy.coordinates import SkyCoord

import gammapy
from gammapy.maps import Map, MapAxis, WcsGeom
from gammapy.data import EventList, DataStore
from gammapy.catalog import SourceCatalog3FHL as catalog
from gammapy.analysis import AnalysisConfig
from gammapy.modeling.models import Models

import os

In [2]:
os.chdir("../1dc/models")

In [3]:
sky_models = Models.read("models_gps_1dc_0_18_2.yaml")

Invalid value BUNIT='1/MeV/cm^2/s/sr' in FITS header. Setting empty unit.
Invalid value BUNIT='1/MeV/cm^2/s/sr' in FITS header. Setting empty unit.
Invalid value BUNIT='1/MeV/cm^2/s/sr' in FITS header. Setting empty unit.
/home/gert/.local/lib/python3.7/site-packages/astropy/units/quantity.py:1032: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  out = super().__getitem__(key)
/home/gert/.local/lib/python3.7/site-packages/astropy/units/quantity.py:1054: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  self.view(np.ndarray).__setitem__(i, self._

In [4]:
for m in sky_models:
    if 'template' in m.spatial_model.tag:
        print(m.name)
 
        mask = m.spatial_model.map.data<0
        if np.any(mask):
            m.spatial_model.map.data[mask] = 0.
            print( "negative values removed")
        print("\n")
        

IEM


Fermi bubbles


DM_GC


DM_Draco


DM_CanesVenaticiI


Westerlund1_gas


PuppisA


Vela X hard


Vela X soft


Vela Junior


RX J1713.7-3946
negative values removed


HESS J1801-233


HESS J1800-240A


HESS J1800-240B


HESS J1800-240C




In [5]:
for m in sky_models:
    if 'template' in m.spatial_model.tag:
        print(m.name)
 
        mask = m.spatial_model.map.data<0
        if np.any(mask):
            m.spatial_model.map.data[mask] = 0.
            print( "negative values removed")
        print("\n")
        

sky_models.pop("DM_Draco")
sky_models.pop("DM_CanesVenaticiI")


i = 0
len_sm = len(sky_models)
while i < len_sm:
    if not sky_models[i].temporal_model == None:
        sky_models.pop(i)
        len_sm -= 1
        print("popped " + str(i))
    else:
       i += 1

IEM


Fermi bubbles


DM_GC


DM_Draco


DM_CanesVenaticiI


Westerlund1_gas


PuppisA


Vela X hard


Vela X soft


Vela Junior


RX J1713.7-3946


HESS J1801-233


HESS J1800-240A


HESS J1800-240B


HESS J1800-240C


popped 1782
popped 1784
popped 1794
popped 1803
popped 1804
popped 1807
popped 1822
popped 1822
popped 1826
popped 1858
popped 1864
popped 1880
popped 1882
popped 1889
popped 1908
popped 1911
popped 1916
popped 1926
popped 1945
popped 1960
popped 1992
popped 1997
popped 1999
popped 2013
popped 2020
popped 2020
popped 2022
popped 2027
popped 2028
popped 2049
popped 2050
popped 2053
popped 2057
popped 2066
popped 2067


In [6]:
en_ax = MapAxis.from_bounds(1,100, nbin=2, unit="TeV", interp="log", name="energy_true")


tot_map = Map.create(width=40, frame="galactic", axes=[en_ax])

In [22]:
tot_map.quantity = sky_models[0].evaluate_geom(tot_map.geom)
i = 1
l = len(sky_models)
l = 15
while i < l:
    
    component = sky_models[i]
    quant = component.evaluate_geom(tot_map.geom)
    nans = np.isnan(quant)
    quant[nans] = 0 
    
    tot_map.quantity =  tot_map.quantity + component.evaluate_geom(tot_map.geom)
    
    if i%5 == 0: print("done " + str(i))
    
    i += 1


done 5
done 10


In [23]:
#q = sky_models[3].evaluate_geom(tot_map.geom)
#qi = np.isnan(q)
#qn = q.copy()
#qn[qi] = 0



In [24]:
rc_params = {
    "figure.figsize": (12, 5.4),
    "font.size": 12,
    "axes.formatter.limits": (2, -2),
}

tot_map.plot_interactive(add_cbar=True, rc_params=rc_params)

interactive(children=(SelectionSlider(continuous_update=False, description='Select energy_true:', layout=Layou…